In [1]:
import sys
import pandas as pd
import numpy as np
import scipy.sparse as sparse
from scipy.sparse.linalg import spsolve
import random

# Data Preprocessing for Matrix User x Item

In [2]:
#Source Code for data Processing
#https://gist.github.com/victorkohler/f48ea6512058719ba52053851fedc745

train_data = pd.read_csv('data/train.csv')
test_data = pd.read_csv('data/test.csv')

In [3]:
#np.shape(train_data)
np.shape(test_data)

(3782335, 12)

In [4]:
#train = train_data.append(test_data)
#np.shape(train)

In [5]:
item_metadata = pd.read_csv('data/item_metadata.csv', sep=',', engine='python')

In [6]:
train_v2 = train_data[train_data['action_type']=='clickout item']
train_v2= train_v2[train_v2.reference.notnull()]
train_v2.head()

user_id     session_id   timestamp  step    action_type reference  \
29   01R92KASN25O  62991f7c78f27  1541055672     8  clickout item   7818446   
32   026J2T90PT57  67c4d45f56146  1541105688     1  clickout item   2681512   
39   032W52V15J3A  e84393cf62d13  1541102603     7  clickout item    929533   
73   03F93632Y45U  f09aa370de0af  1541109160    34  clickout item   8496296   
393  08527D0MD8VC  3e2a95e5727f9  1541099104   320  clickout item   8266350   

    platform                     city   device current_filters  \
29        DE         Luebeck, Germany   mobile             NaN   
32        MX  Ezequiel Montes, Mexico   mobile             NaN   
39        HR           Cancun, Mexico   mobile             NaN   
73        US           San Diego, USA   mobile             NaN   
393       ES         Lisbon, Portugal  desktop             NaN   

                                           impressions  \
29   7818446|51315|2133708|119638|86359|133581|6688...   
32   6010044|5433188|5156000|4780400|5137162|992819...   
39   3132957|100226|1954167|9462680|2776177|929533|...   
73   9112592|102414|9140448|5654906|4341120|9739716...   
393  3505518|1834297|4837106|3990396|2042495|486747...   

                                                prices  
29   163|75|93|98|169|201|129|117|108|170|133|80|87...  
32   38|35|54|37|73|37|37|30|71|75|64|26|25|37|40|3...  
39   25|324|67|52|57|21|90|240|64|37|70|60|167|45|6...  
73   263|114|263|273|122|194|236|161|219|113|110|19...  
393  47|50|45|40|45|40|40|50|50|45|50|45|38|49|48|3...

In [7]:
train_v2.dtypes

user_id            object
session_id         object
timestamp           int64
step                int64
action_type        object
reference          object
platform           object
city               object
device             object
current_filters    object
impressions        object
prices             object
dtype: object

In [8]:
train_v2["reference"]= train_v2["reference"].astype(int)
train_v2["step"]= train_v2["step"].astype(int)
train_v2.dtypes

user_id            object
session_id         object
timestamp           int64
step                int64
action_type        object
reference           int64
platform           object
city               object
device             object
current_filters    object
impressions        object
prices             object
dtype: object

In [9]:
train_v2.head()
#np.shape(train_v2)

user_id     session_id   timestamp  step    action_type  reference  \
29   01R92KASN25O  62991f7c78f27  1541055672     8  clickout item    7818446   
32   026J2T90PT57  67c4d45f56146  1541105688     1  clickout item    2681512   
39   032W52V15J3A  e84393cf62d13  1541102603     7  clickout item     929533   
73   03F93632Y45U  f09aa370de0af  1541109160    34  clickout item    8496296   
393  08527D0MD8VC  3e2a95e5727f9  1541099104   320  clickout item    8266350   

    platform                     city   device current_filters  \
29        DE         Luebeck, Germany   mobile             NaN   
32        MX  Ezequiel Montes, Mexico   mobile             NaN   
39        HR           Cancun, Mexico   mobile             NaN   
73        US           San Diego, USA   mobile             NaN   
393       ES         Lisbon, Portugal  desktop             NaN   

                                           impressions  \
29   7818446|51315|2133708|119638|86359|133581|6688...   
32   6010044|5433188|5156000|4780400|5137162|992819...   
39   3132957|100226|1954167|9462680|2776177|929533|...   
73   9112592|102414|9140448|5654906|4341120|9739716...   
393  3505518|1834297|4837106|3990396|2042495|486747...   

                                                prices  
29   163|75|93|98|169|201|129|117|108|170|133|80|87...  
32   38|35|54|37|73|37|37|30|71|75|64|26|25|37|40|3...  
39   25|324|67|52|57|21|90|240|64|37|70|60|167|45|6...  
73   263|114|263|273|122|194|236|161|219|113|110|19...  
393  47|50|45|40|45|40|40|50|50|45|50|45|38|49|48|3...

In [10]:
#train_v3 = train_v2.head(10000)
train_v3 = train_v2
train_v3.head()
np.shape(train_v3)

(1586586, 12)

In [11]:
data = train_v3[['user_id','reference']]
data.head()
#np.shape(data)

user_id  reference
29   01R92KASN25O    7818446
32   026J2T90PT57    2681512
39   032W52V15J3A     929533
73   03F93632Y45U    8496296
393  08527D0MD8VC    8266350

In [12]:
data=data.groupby(['user_id','reference']).size().reset_index()
data.columns = ['user', 'item', 'click_count']
data.head()

user     item  click_count
0  0001VQMGUI65   477811            1
1  0001VQMGUI65   950829            1
2  0001VQMGUI65  2019467            1
3  0001VQMGUI65  3133074            2
4  0003QTCX5MJX  2195060            1

In [13]:
user_id_table = data['user']
user_id_table = pd.DataFrame(user_id_table)
user_id_table = pd.DataFrame(user_id_table['user'].unique())
user_id_table.columns = ['user']
user_id_table['user_id'] = dict(enumerate(user_id_table['user'], start=0))
user_id_table.head()
#np.shape(user_id_table)

user  user_id
0  0001VQMGUI65        0
1  0003QTCX5MJX        1
2  0004IOZI7CKF        2
3  0004WCFRV3FB        3
4  0006W0R5A5V8        4

In [14]:
item_id_table = data['item']
item_id_table = pd.DataFrame(item_id_table)
item_id_table = pd.DataFrame(item_id_table['item'].unique())
item_id_table.columns = ['item']
item_id_table['item_id'] = dict(enumerate(item_id_table['item'], start=0))
item_id_table.head()
#np.shape(item_id_table)

item  item_id
0   477811        0
1   950829        1
2  2019467        2
3  3133074        3
4  2195060        4

In [15]:
data = data.merge(user_id_table, how='left', left_on='user', right_on = 'user').merge(item_id_table, how='left', left_on='item', right_on = 'item')
data.head()
#data = data[["user_id", "item_id","clickcount"]]
#data.head()

user     item  click_count  user_id  item_id
0  0001VQMGUI65   477811            1        0        0
1  0001VQMGUI65   950829            1        0        1
2  0001VQMGUI65  2019467            1        0        2
3  0001VQMGUI65  3133074            2        0        3
4  0003QTCX5MJX  2195060            1        1        4

In [16]:
data2 = data[["user_id", "item_id","click_count"]]
data2.head()

user_id  item_id  click_count
0        0        0            1
1        0        1            1
2        0        2            1
3        0        3            2
4        1        4            1

In [17]:
#Based on the implementation from https://github.com/ivallesp/deep_matrix_factorization
def batching(list_of_iterables, n=1, infinite=False, return_incomplete_batches=False):
    list_of_iterables = [list_of_iterables] if type(list_of_iterables) is not list else list_of_iterables
    assert(len({len(it) for it in list_of_iterables}) == 1)
    l = len(list_of_iterables[0])
    while 1:
        for ndx in range(0, l, n):
            if not return_incomplete_batches:
                if (ndx+n) > l:
                    break
            yield [iterable[ndx:min(ndx + n, l)] for iterable in list_of_iterables]

        if not infinite:
            break

In [18]:
#Based on the implementation from https://github.com/ivallesp/deep_matrix_factorization
import tensorflow as tf
import numpy as np

class DeepFactorization():
    def __init__(self, n_users, n_items, emb_size, lr=0.001, _lambda = 0.1):
        self.lr = lr
        self._lambda = _lambda
        tf.reset_default_graph()
        self.ph_keep_prob = tf.placeholder(dtype=tf.float32, shape=(None), name="keep_prob")
        self.ph_u_ids=tf.placeholder(dtype=tf.int32, shape=(None,), name="u_ids_ph")
        self.ph_i_ids=tf.placeholder(dtype=tf.int32, shape=(None,), name="u_ids_ph")
        self.ph_y = tf.placeholder(dtype=tf.float32, shape=(None, 1), name="y")
        self.u_emb = tf.get_variable(shape=(n_users, emb_size), name="U_Embedding")
        self.i_emb = tf.get_variable(shape=(n_items, emb_size), name="I_Embedding")
        self.u_bias = tf.get_variable(shape=(n_users, 1), name="U_Bias")
        self.i_bias = tf.get_variable(shape=(n_items, 1), name="I_Bias")
        u=tf.nn.embedding_lookup(self.u_emb, self.ph_u_ids) #+ tf.nn.embedding_lookup(self.u_bias, self.ph_u_ids) 
        i=tf.nn.embedding_lookup(self.i_emb, self.ph_i_ids) #+ tf.nn.embedding_lookup(self.i_bias, self.ph_i_ids)
        ub=tf.nn.embedding_lookup(self.u_bias, self.ph_u_ids)
        ib=tf.nn.embedding_lookup(self.i_bias, self.ph_i_ids)
        ub=tf.nn.dropout(ub, self.ph_keep_prob)
        ib=tf.nn.dropout(ib, self.ph_keep_prob)
        u=tf.nn.dropout(u, self.ph_keep_prob)
        i=tf.nn.dropout(i, self.ph_keep_prob)
        self.mfac = tf.reduce_sum(u*i + ub + ib, axis=1, keepdims=True)
        self.mfac = tf.nn.dropout(self.mfac, self.ph_keep_prob)
        emb = tf.concat([u, i], axis=1)
        emb = tf.nn.dropout(emb, self.ph_keep_prob)
        h = tf.layers.Dense(128, tf.nn.swish)(emb)
        h = tf.nn.dropout(h, self.ph_keep_prob)
        h = tf.layers.Dense(64, tf.nn.swish)(h)
        h = tf.nn.dropout(h, self.ph_keep_prob)
        h = tf.layers.Dense(32, tf.nn.swish)(h)
        h = tf.nn.dropout(h, self.ph_keep_prob)
        self.output = tf.layers.Dense(1)(h) + self.mfac
        self.loss = tf.losses.mean_squared_error(self.ph_y, self.output)
        self.op = tf.train.RMSPropOptimizer(learning_rate=lr).minimize(self.loss)
        self.sess=tf.Session()
        self.sess.run(tf.global_variables_initializer())
        
    def fit(self, x, y, batch_size):
        batcher = batching([list(x), list(y)], n=batch_size, return_incomplete_batches=True)
        for batch_x, batch_y in batcher:
            self.train_on_batch(batch_x, batch_y)
        
    def train_on_batch(self, x, y):
        u_ids, i_ids = list(zip(*list(x)))                              
        self.sess.run(self.op, feed_dict={self.ph_u_ids: u_ids, self.ph_i_ids: i_ids, self.ph_y: y,
                                          self.ph_keep_prob: 1-self._lambda})
        
    
    def predict(self, x, batch_size):
        batcher = batching([list(x)], n=batch_size, return_incomplete_batches=True)
        preds = []
        for batch_x in batcher:
            batch_x = batch_x[0]
            u_ids, i_ids = list(zip(*list(batch_x)))
            preds.append(self.sess.run(self.output, feed_dict={self.ph_u_ids: u_ids, self.ph_i_ids: i_ids,
                                                      self.ph_keep_prob: 1.0}))
        preds = np.row_stack(preds)
        return preds
    
    def evaluate(self, x, y, batch_size):
        return np.mean((np.round(self.predict(x, batch_size)) - y)**2)

In [19]:
data.head()

user     item  click_count  user_id  item_id
0  0001VQMGUI65   477811            1        0        0
1  0001VQMGUI65   950829            1        0        1
2  0001VQMGUI65  2019467            1        0        2
3  0001VQMGUI65  3133074            2        0        3
4  0003QTCX5MJX  2195060            1        1        4

In [20]:
# Load the data and calculate the users set and items set cardinalities
import itertools

original_itemid = data["item"].tolist()

df = data2
df = df.iloc[:5000,:5000] #slicing for testing smaller sample
U_cardinality,I_cardinality = np.unique(df['user_id']).shape[0], np.unique(df['item_id']).shape[0]
mat = df.values
train_mat = mat
x_train=(train_mat[:,:2])
y_train=(train_mat[:,2:])

DF = DeepFactorization(n_users=U_cardinality, n_items=I_cardinality, emb_size=3, lr=0.002, _lambda=0.1)
losses_train = [DF.evaluate(x_train, y_train, batch_size=200)] # Add the initial loss (w. random weights)
for i in range(50): # Run for 50 epochs
    DF.fit(x_train, y_train, batch_size=128)
    #losses_train.append(DF.evaluate(x_train, y_train, batch_size=128)) # Compute the train performance

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Instructions for updating:
Shapes are always computed; don't use the compute_shapes as it has no effect.
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Use tf.cast instead.


In [21]:
def trivago_item_to_model_item(trivago_item_id):
    """
    Converts an item id on the trivago format over to the id in the model.
    
    trivago_item_id: int
    returns: int
    """
    for model_item_id in range(len(original_itemid)):
        if original_itemid[model_item_id] == trivago_item_id:
            return model_item_id
    raise Exception("There's no item with trivago item id", trivago_item_id)

In [22]:
def model_item_to_trivago_item(model_item_id):
    """
    Converts an item id on the model format over to the id in trivago.
    
    model_item_id: int
    returns: String
    """
    
    try:
        return original_itemid[model_item_id]
    except:
        raise Exception("There's no item with model item id", model_item_id)

In [23]:
def trivago_user_to_model_user(trivago_user_id):
    """
    Converts a user id on the trivago format over to the id in the model.
    
    trivago_user_id: int
    returns: int
    """
    original_userid = user_id_table["user"].tolist()
    for model_user_id in range(len(original_userid)):
        if original_userid[model_user_id] == trivago_user_id:
            return model_user_id
    raise Exception("There's no user with trivago user id", trivago_user_id)

In [24]:
def model_user_to_trivago_user(model_user_id):
    """
    Converts a user id on the model format over to the id in trivago.
    
    model_item_id: int
    returns: String
    """
    original_userid = user_id_table["user"].tolist()
    try:
        return original_userid[model_user_id]
    except:
        raise Exception("There's no model user with user id", model_user_id)

In [3]:
import random
import csv
import operator
import os.path


class Submission:
    """
    Find the predicted top ratings and writes it to a file in the format specified by the RecSys challenge.
    """

    def sort_items(self, user, items):
        """
        Given a user and a list of items, this method predicts the user's rating for these items and 
        return a sorted list of the items in descending order of the item's predicted ratings.
        """
        
        try:
            model_user_id = trivago_user_to_model_user(user)
        except:
            # If the user is not known to the system, we submit the accomodations in the impression list
            return items
        
        x = (model_user_id,)
        y = list(range(50))
        
        # DF.predict crashes with this user InvalidArgumentError: indices[0] = 2797 is not in [0, 2789)
        if model_user_id > 2789:
            return items

        user_item_iterable = list(itertools.product(x, y))
        print(user_item_iterable)
        predictions = DF.predict(user_item_iterable,200)
        
        # Creates a dict with item id as key and predicted rating as value
        item_dict = dict()
        for j in range(len(predictions)):
            item_dict[original_itemid[j]] = predictions[j][0]
        
        # Creates a list of the top 25 recommended hotels
        sorted_item_list = sorted(item_dict, key=item_dict.get, reverse=True)[:25]
        
        # Converts items in list from int to String
        for i in range(len(sorted_item_list)):
            sorted_item_list[i] = str(sorted_item_list[i])
        
        return sorted_item_list
    
    def write_header_line(self):
        
        i = 0
        while os.path.exists('submissions/submission-' + str(i) + '.txt'):
            i += 1
        self.submission_file = 'submissions/submission-' + str(i) + '.txt'
        
        
        with open("dmf/submission.csv", mode="w") as submission:
            recommendation_writer = csv.writer(submission, delimiter=',', quotechar='"', 
                                               quoting=csv.QUOTE_MINIMAL)
            recommendation_writer.writerow(["user_id", "session_id", "timestamp", "step", 
                                            "item_recommendations"])

    def write_line(self, user_id, session_id, timestamp, step, recommendations):
        """
        Writes a line in the submission file.
        :param recommendations: The list of recommendations in descending order
        """
        
        with open("dmf/submission.csv", mode="a") as submission:
            recommendation_writer = csv.writer(submission, delimiter=',', quotechar='"', 
                                               quoting=csv.QUOTE_MINIMAL)
            recommendation_writer.writerow([user_id, session_id, timestamp, step, " ".join(recommendations)])

    def write_submission_file(self):
        """
        Generate and writes the file that is submitted to the RecSys challenge.
        """
        self.write_header_line()
        
        not_in_model = 0
        model_small = 0
        model_big = 0

        with open("data/test.csv") as test:
            reader = csv.reader(test)
            for row in reader:
                action_type = row[4]
                if action_type == "clickout item":
                    reference = row[5]
                    if not reference:
                        # This is the line is missing the click-out item. Generating recommendations for 
                        # this user.
                        user_id, session_id, timestamp, step = row[0:4]
                        print(user_id)
                    
                        
                        try:
                            model_id = trivago_user_to_model_user(user_id)
                            if model_id < 2789:
                                model_small += 1
                            else:
                                model_big += 1
                        except:
                            not_in_model += 1
                        
                        items = row[10].split("|")
                        recommendations = self.sort_items(user_id, items)

                        # Writes the result to file
                        self.write_line(user_id, session_id, timestamp, step, recommendations)
        print(not_in_model)
        print(model_small)
        print(model_big)



In [4]:
sub = Submission()
sub.write_submission_file()

000324D9BBUC
0004Q49X39PY
0004Q49X39PY
00071784XQ6B
0008BO33KUQ0
000GO9NY6P4M
000IRHJS2DL9
000JB0UNEH23
000OWRCYEHKT
000VBY1D6BP8
00130PO6XSZR
0013L641G5P2
0015X90DOWT1
0017FIR55K7R
001D536Q4S8D
001I0INS8EBP
001LT4KVZ14I
001P60T145X4
001TD1JLUE4D
001WP37I7I1T
001XGI2NI73R
0020N6R8BEDO
00210VAF61G5
0022L3757L7J
0023UTXOFLJP
0028DFS9FKIP
0029BRXGBS69
0029FEXX2R5F
002BISXP1U1Q
002CQHIQ78E8
002CUWLQDUV7
002DU3SR91P5
002EOD1A549M
002H6CBQZ649
002N9ZH16N1R
002NTOHZ5ED7
002T8HU4LZAS
002XKX4GXZ4T
002YMA0MBZRU
0034995IC4NO
0037C9PR4SF5
003A3JYSRGG8
003B331S7UDW
003F9HSS9A74
003GTU93A7FX
003QACWP50CH
003X06KWBDX5
003XRCCDD37S
00403ZK4RGNZ
00407X218KLB
00488C3ETUAP
0048L9BIU43N
0048PS2O6H4C
0049QZLKZEHB
004A07DM0IDW
004CO1YD7CIJ
004LXF1R1T52
004R06H8JVMI
004U1C778DFX
004XLJ0YHOGO
0051DEO9I24S
0058BVPZ9B4U
005AB67JG86V
005E85QJB7AW
005LKOE5KTXA
005QC80N413F
0060UNDWIR40
0064SEVCILE0
006GIDK43GQ4
006JCAYA1Q4I
006LBV913YC5
006M0J0XA767
006U1MLZ9FJN
006Z7IRZ5OKM
0071UCFVZYD1
007618DAVP32
007648LAD0QX

03F8HRAGKSBY
03F93632Y45U
03FH4046B956
03FY1470RIIG
03GOBVPMZQL6
03GQ3RSJ2XWD
03GS67365E4G
03HDE3LA40P0
03HOAJ57G84H
03HTQYGJTX88
03HXWN45HRWK
03I34DUYFGA1
03I3954KHXM0
03I4AHPLQTS4
03I52OS2X53V
03ICB15XO4N0
03IJ2NHNMUSH
03IMWJW9PDKQ
03IN6GSYMFLC
03IQFBAP3DT1
03IT9PO22W0O
03J4TJE93579
03J7P8ZY9AY0
03JFXGUQLIDT
03JP02YTSM0L
03JS3RMHP26R
03JUWWRX0B95
03K49ZMT0HTP
03K8RAG7BVT7
03K9QX7WURJG
03KI773LBO5R
03KNTPZPXC9O
03L2RM6AWWAX
03L3TBFRHHYQ
03L4DGKLGPWB
03L8EBYI34VO
03LDCBZZM5G5
03LKXF2P8264
03LM9AHP770X
03LO91QAZFRL
03LOO2DPMO9W
03LP18LDR448
03LTH89QY623
03LTXHG5AF8W
03LVHC6RAGRX
03M81Y3LVVZ7
03M9MIJN71UY
03M9MIJN71UY
03MAVA22KH3O
03N345EWK25U
03N43METJDO6
03N7AFSA6C48
03N82I257L6L
03NC17UD9EE1
03NEET6E049F
03NG21WKNOSG
03NHC36UXD4Y
03NJPXHA8JWK
03NK4UWGXV9P
03NTHHEEWWPW
03NVPHS0JJBC
03NZ18LW6J31
03O3DWE9OID8
03O97ZQ3HR5D
03O9X29NKJT5
03OF6VINQJPF
03OFPGRDD0E0
03OLKADF2MEA
03ON5PTUE454
03OPV6ZYXMFX
03OQ2RQLYOQB
03PEF45XT5CD
03PI704W4FO6
03PJKF1CYBMI
03PK9FWDGVW4
03PO2ZP7H8JZ
03PT8Q2L3LJI

05U71KAJM57O
05U8ZYOC85NY
05UG2OL7JVS4
05UI9VZZNJS7
05UM93MRVZAC
05UQ13GTUF6O
05UUIH30JH3X
05V498NG37CV
05V5SCTEMS8R
05V8Q2WJ5WD4
05V9AHTEALW7
05V9DZ60VRRR
05V9HY62EREQ
05VHCQQA54WO
05VHY8T4LZ04
05VKJHS6042Y
05VNZK61JAR0
05VRP5O5LKCP
05VS411UWX0K
05VWO2C65C23
05W4NFM7VXK9
05W56VTHMU0I
05W5CM4OXBEJ
05W5YA9MG21B
05W9ZU33GM2E
05WFLZPL84QG
05WFWWPIXR78
05WQ6XR9M3YX
05WRGS41GX2J
05WRUA48HG8G
05X1AP183YLM
05X49S3ITIXD
05X4MGH8O87H
05X5N4WJ0R7J
05X987B41MHD
05XCL6TR22B6
05XKXU2P8Y8X
05XR481LP537
05XRYP4WIL6V
05Y32G6GA5DL
05Y4W99CUNC5
05Y5C07JZ9AI
05Y6AU2JO828
05YA8AIQV1MC
05YPWEXWRX4H
05YRIC5K1CRC
05YU545MYNUE
05YXT8RNQRA6
05Z0O1KQG5GO
05Z6IPXQ53VC
05Z7VJYXPPVG
05ZCVYUA050C
05ZFW3R9HPRV
05ZJN0PACA97
05ZK1JO9A4Z2
05ZVHBH3RRTV
06002YFSVKVC
06008B5603J8
0600UXE4T2DV
0601MW62KE6N
0604JARKN6MP
060825TTCTD5
060C7WT9G6L3
060G17Z93QYW
060KOJKRDL64
060R2SKBV08Z
0610J8JCJA60
0611203LBOH8
0612CUPTSRXN
0614OYJXS7TE
0615HOCSP50B
0619UG68WH29
061FAC3UDZGZ
061FL9TUN093
061GONZUQFZE
061JLOLB6W7F
061N8J9NYPBZ

096TB3E0X5SW
09745QXH0SX6
0977B4992IP2
09783TJCGWWB
0979G4SNF49G
097JPUCPWAUU
097RISWQM22I
097V5IE6N4PD
097Y3LP2ZENJ
0981KEV4IOYQ
09861M8W00MA
098FQTUPZULA
098IMPAV6LTY
098IPKRD84XM
098J0XZC6RMI
0990T6M8UQIL
0992SZ98DZU7
0992SZ98DZU7
09938XFFD288
099514M1RVVK
0998FQQG5W21
0999Y38IJP3K
099J3D2J1CIL
099JS0RUDQX5
099KWH89XSQ5
099LAWGAH1HK
099PG4GUDDG4
099SHTU82QGE
099TDXSQN9C2
09A3P9ZF0260
09A6QDI0UGC9
09A77AG2U1RO
09A9KI9BF71U
09AAM0RQ1N5U
09ACO2MX8P2Y
09AD6V5F9GMY
09AH1QJYPLRT
09AOHYO5POSF
09ARZ4S21XWO
09BD7MWG9DL6
09BZ90YRJBA6
09BZTJBC315U
09C8FSQ259WX
09C9B162XFGB
09CBXP8KX3RV
09CD4U0425W0
09CH4YO4XK62
09CJDZ3R0JIY
09CW8IDYMBHO
09CYHJYRZ7MU
09D71X52I9W0
09DCFXZ54YV8
09DK3A0DLU73
09DL7E7A2I2K
09DNTG5D1OH5
09DOEZL4VVPM
09DOYO38I623
09DWV16C7ZRE
09DWYXSEDZJO
09E222KWW62O
09E3FLK2BBV1
09EI2PM3ETKX
09EN36CB3B86
09EOAL6D17J0
09ETO85J3WPS
09EUIRX3SYUL
09EV16W5UXR7
09EY7QBC6956
09F0QJND2YHU
09F1O7MWHJ6A
09F2FCHMYR7U
09F67L6QGGF7
09F9ONU42U1X
09FA1D47T8DT
09FAGTQ8V90F
09FDAXR92RVE
09FE0FIZO63H

0E3T3OULE39N
0E3U5UFNCNLY
0E40F3Y7303Q
0E4715215W3Z
0E4HAC1HOIGW
0E4L3JTJ60U7
0E4WWWCL3TPG
0E53HB5DRU8I
0E53TB7YRB84
0E56SMH8F9O9
0E58VKF37XT0
0E5QFMWK3W3U
0E5WSRV8SQ32
0E6DJO76UJDC
0E6HQBLA8TP4
0E6I8UTH1SJ2
0E6L1CJN4OW0
0E6QCRWSK4IB
0E6TDBXPOMBN
0E6TXIF6QO27
0E6VY2GA6T1X
0E6WKW622ODL
0E78URCFGADX
0E78URCFGADX
0E78URCFGADX
0E797SBJKT9R
0E79SZYK9H0L
0E7ATW7O5P0P
0E7ATW7O5P0P
0E7CFE982PCM
0E7D6YQZCAX8
0E7F9M42YEB3
0E7MO03H3H5F
0E7N55TZ99K2
0E7QVT9FX35T
0E7R0I7JLYE3
0E7R5I7R7DZ2
0E7S8A82GZAM
0E7SKE1V6IWW
0E7V4YWONT8Z
0E82IYN04WFF
0E8434RV7TKY
0E84C5J0R8OZ
0E86UUVYB3W1
0E8BVM25B23V
0E8HL76DGPK1
0E8I20DVILU6
0E8JQK80GB4Q
0E8JS1CIKS82
0E8KX7M53QEG
0E8YLZSIBXTI
0E8YOQJ31K4S
0E95QL5750HR
0E96BLP16LWB
0E987PW9KPRW
0E9DEHPCAAK8
0E9J8J7SU3V8
0E9RWAP7X4Q4
0E9UMRGU4JMN
0EA5ILFR15NK
0EA5QD0Z80IK
0EA97KXNZZ7P
0EAJSW70PBDH
0EAQFBLZO4X1
0EAVW0UFY1CY
0EAWLLTLFRNS
0EBP5BNFPCZM
0EBS4C620CH9
0EBYMU3ULL4J
0EBYOYZKBW29
0EC01ST8NK24
0EC63I3RGVF1
0ECBSQL630E4
0ECL5LA0O25I
0ECQKNG0SW8X
0ECQSXNHKSOB
0ECSMCCRBWZF

...

Z0RL225J0DN6
Z0RWT6CNZKCX
Z0S2UDP19WSV
Z0S6B66Z2L2O
Z0S81VKO69FT
Z0SA6R021VX5
Z0SIYZWSDJ1G
Z0SSD7C37MYX
Z0SWZM7QOBGT
Z0T4P0DVPCIV
Z0TBZC275UYO
Z0TEINCXPIGB
Z0TVR3QM9MRD
Z0U1HJ8VOV1X
Z0U1HJ8VOV1X
Z0US73S6GK1Y
Z0UTT900XZEG
Z0UXNNPW6OP0
Z0UZ4MDW698P
Z0V1EP7V2MPP
Z0VR7BD63L9S
Z0VY0ATZFO1V
Z0VYAQBYORJZ
Z0W39S32CSU0
Z0W850Y8BE95
Z0WA56DDA2FV
Z0WR7J3J83A3
Z0WYQPB2ZAAS
Z0X3QWCFHTS1
Z0X4GM8MG6ZA
Z0X4SVDBQJDY
Z0X8SECBZZKP
Z0XB34RFDHYR
Z0XF64NJ91EX
Z0Y9S1LK1AIC
Z0YBSK839FBT
Z0YKOHSHDKE1
Z0YMY9Z294C3
Z0YOYRX55T1D
Z0YP61T0KR9G
Z0YQ90V8SKMA
Z0YQJCTD7QQ6
Z0YUA5JJFQ77
Z0YZWPM2CKOT
Z0Z4GS3FDI13
Z0ZACN7E0ZOP
Z0ZGI9WUFM25
Z0ZIR08J2TCY
Z0ZJEBB40QQQ
Z0ZKHV8IHT39
Z0ZMQS2J0YH6
Z0ZN620YQZD8
Z1042KMHT444
Z105E5Q0TUYH
Z10D5R3QVICG
Z10F7EE0RI0E
Z10F7EE0RI0E
Z10H2IGWP19E
Z10PVKX22768
Z11A30TSZW16
Z11O3RGEIFRA
Z11QD04C0Y3C
Z11XO4X4L33L
Z11Y5T0F7V9L
Z1250N7OAMRV
Z129GENLDX82
Z12D0R8WRT95
Z12LGWMVPC95
Z12N9Y0USFYM
Z12NI485BU71
Z12O8ERJL8H8
Z12T5X9TU084
Z12XMP8WANEB
Z136N3JX5M5Z
Z137F7UW83DQ
Z138I8LY95B9
Z13IA7P7CPPU

Z74VB476KR3V
Z75691ZX7R7J
Z756IVYWN9HQ
Z75EATIL5TU1
Z75FDLY9I3YK
Z75GX7XC539D
Z75N0YRTPN8B
Z75Q8VIY75KS
Z75QLZFAG6ZS
Z75U406QV1P8
Z75WJDUFNGIZ
Z763Q32G827Z
Z763XV92SFA8
Z767841D5EF2
Z76HJ5C89C24
Z77NQE0FXEOW
Z77PMZI7VK93
Z7807KLK0IF8
Z784S7EOZ9JK
Z78BZXPZI6A0
Z78NGW0E5WG1
Z78PRD0P91ZP
Z78XFU79IL8O
Z78ZGYJG9PMU
Z79A3LL8FGYX
Z79BMWFLJQ4X
Z79FGE61PCGZ
Z79HCAQAPPBM
Z79L8D1BH6T1
Z79R2660QLRJ
Z7A396WBV03G
Z7AIBCE3A43E
Z7AV8WXOK7K5
Z7AVP9ODVRQZ
Z7AXCJKVUU47
Z7B6U56FZDXB
Z7BCFVR1MCHR
Z7BD3WMX1RWD
Z7BDMNH489W9
Z7BF5GYFAURH
Z7BH4TO8POIK
Z7C0Z8P4WI9Z
Z7C6621C383O
Z7C7M7L6T78D
Z7C8B8CW8619
Z7C9AU928K41
Z7D3R0OZTF7I
Z7D4VW37KFJQ
Z7D51UWCV41W
Z7D9H6YZ5WEM
Z7D9ZTHGZ703
Z7DMLV8M4ZKK
Z7DMPDMAJAF2
Z7DZMP5IY31K
Z7E32AMO13V7
Z7E73VCZ7PM6
Z7EVM73DN44Q
Z7F203A27B30
Z7FJS8JFT9TN
Z7FL6J38UZBL
Z7GAILXB1SZN
Z7GHUMT14MKZ
Z7GS17XL1R1G
Z7GY197P7WLN
Z7H1X624Y73D
Z7H39BPOD9WB
Z7H6WZBWLCXT
Z7HBAR8JJKLP
Z7HH3K8YKDZ8
Z7HJ9K321GAF
Z7HM3I5IXM49
Z7HP0R60W6IA
Z7HWFQJ440KO
Z7I0N2KZBYC7
Z7I1YORTCTAX
Z7I2TG6XID5E
Z7IC57C2ATCD

ZEM501QEJVCF
ZEMO5HT434PV
ZEMP9X5LTCNX
ZEMSA05P6CE5
ZEMX9J8MB4X7
ZEN17ECXNB99
ZENEHM0GKATJ
ZENEXGPS9446
ZENP69NGJQRA
ZEO26M3JZO2A
ZEO9ZCZLCPSN
ZEOEBWDFISBD
ZEOPAALWT60Z
ZEOWOBYCJ8G2
ZEP64LULZXVL
ZEPFHJUG9D1B
ZEPL1MQ4R944
ZEPVTJUWTLW8
ZEQDIA37PXX5
ZEQLGNXNUFXM
ZEQZHOPMGJE9
ZERA6E97K0SD
ZERA8PW8UKB2
ZERFSDGGJFE3
ZERNKA15GY1V
ZERNR5459PMQ
ZERSQ53K1SZE
ZES4ZPEVKDK1
ZES9Y5O0FT47
ZET0SKPYR9A7
ZET712QYGL57
ZET83QV7IGFF
ZETQH2MQIFK4
ZETSCMO2SRBM
ZEUEWYGP8S08
ZEUEWYGP8S08
ZEUNCA14UHQV
ZEV0IN6DGS8P
ZEV0XFP874SI
ZEVRY9YHVTB4
ZEVY84N4D37Y
ZEW187TN7317
ZEW3IDLVAU8A
ZEW84V1LQBF5
ZEWDF3IDPFFO
ZEWQ3DC7TCIH
ZEWRTIGBV76M
ZEWYLVVTF6S5
ZEX2AYIH16LB
ZEXI9CAYJM60
ZEY95W48M0CT
ZEYK69Q77SVS
ZEYUV13T6CLQ
ZEYVLADRR19H
ZEZ3NVOSH00G
ZEZJF9461C2N
ZEZKGB0EHT12
ZEZOR1I7BCRC
ZEZOYJQOU4ER
ZEZP4W8OT1YQ
ZF02ILWYW79E
ZF078VKO5Q58
ZF07QB07N0AL
ZF0GP22YJ1CG
ZF0YJY2854YY
ZF122AMGZTAB
ZF1FNF4VX993
ZF25I0DHK8JQ
ZF2CU5WN3WVI
ZF2OSRXY5IL5
ZF2P4MG0NBN4
ZF34BWRMS37R
ZF38KRL7UYE1
ZF39J84A1XNC
ZF3TF3I550KD
ZF42R0QTC0T6
ZF469CC17D7F

ZM93FG7QWBAA
ZM93KWS2WGVA
ZM9BBT4ZLBJM
ZMA05BD8BIS4
ZMAEG5EOO9J6
ZMAK1A0PQ8EC
ZMBKVC03ZFE6
ZMBQE33DQUFF
ZMBZ52ZTX35O
ZMC3TL359MBA
ZMCCHQOOAQMG
ZMCD1C98E9E9
ZMCDB31B9BUK
ZMCOW0EH694N
ZMD6Z0Q244SN
ZMD6Z0Q244SN
ZMDMQBKQCPEO
ZMDW1WPCABGW
ZMDYJR03JM4V
ZME3STM9XW7T
ZME45QC86NT9
ZME45QC86NT9
ZME47EWM8OCT
ZMEM9XM6ENWP
ZMEPCXWIEN91
ZMF24E2LI0KT
ZMF2B7NTP7MM
ZMF4KNK7OYPE
ZMF4LT03Y9X3
ZMF7RE4PWN92
ZMFK0O7NB1Z9
ZMFSE3NTYV36
ZMFWC5H81XV5
ZMG72QRQ15R9
ZMG76QE99R9R
ZMGLM4TXNIBU
ZMIJGTDCW51L
ZMIMWDY17P0X
ZMIO2AZ8P5B6
ZMIP0Q2RHVF3
ZMIXECKCBINC
ZMJOJAGLWYHL
ZMK1M6GIJ2U6
ZMKEEZWEVV0R
ZMKL1LEVZ0KW
ZMKNQ6VG98KB
ZMKY5N0SEIQ5
ZMKYHSJ2DFSH
ZMKYJ1S6559F
ZML2D4PA38Y6
ZML8NF0179K3
ZML96U87N47A
ZMLEFPSU69VT
ZMLMJIAX380Q
ZMMR3JIKD6J5
ZMN2SOPTXFK8
ZMN5DDL29X3H
ZMN86ZLXMB4F
ZMNCQP2WC7M3
ZMNKJVGQD6AL
ZMNRP87HLGYA
ZMO0IKY8RIQR
ZMO8EYXLHAJJ
ZMO95JYX0ZIP
ZMODRCY8WI50
ZMONHBDKEDN8
ZMOP2FU817Q0
ZMP9EXY8S5D4
ZMPLFV1PN0QV
ZMPS24VE3N8P
ZMQ5KUJQI05R
ZMQQ1AOQKBB0
ZMQUHLHQZJKU
ZMQZJYK00NXC
ZMR4SHPX0LM6
ZMR7VP7NK526
ZMRFI95J0ZR4

ZTUZU1KM2O68
ZTV4E99CAL8Y
ZTV6Q8BUJL7I
ZTVD8O5N2L8Z
ZTVI2Z98HQW6
ZTVL1C0QYNJ9
ZTW9YVC7QX9H
ZTWRNZ5082BN
ZTX5J7342SWW
ZTXH85BT1F7J
ZTXHX6P9558A
ZTXR7QHYTBF5
ZTXRGH6Y9JQP
ZTXWF5990UQK
ZTY53RDPU5G0
ZTY5VCLZBSYO
ZTY9G17U0936
ZTYH5K145VX1
ZTYJK2BH6UC8
ZTZFSB55TZV8
ZTZIP56R4NPI
ZTZMYLM0BZ2W
ZTZRL2RVXNKV
ZU01ASRF7JS4
ZU08DS3MPXWM
ZU0QMB7O1QXM
ZU0QWYNZF455
ZU0T71J0KYJP
ZU0V9K1Q27OX
ZU140NKSDVWV
ZU1A8FLNF9FN
ZU1P5TLHOUVZ
ZU1YIRXSGT4L
ZU1ZQOWP5V97
ZU20ZUC1K0VO
ZU27FY6ZP5BJ
ZU30H89R3V82
ZU31FB8S6RJW
ZU33US2TGY22
ZU37B8HAJZ8O
ZU381M3MXTBH
ZU3EIH1UAFWX
ZU3JSHR5R9ZO
ZU3MEPD6O1CS
ZU3PV0H5FY0B
ZU3Q594HMILM
ZU3ZVFC3MSR3
ZU47HSDC38V6
ZU47Q1GBAX88
ZU4A44K24XLW
ZU4DZICSY5G6
ZU4EP49LLJ61
ZU4ZEA3WFSUY
ZU50TFU2XNKG
ZU51B7D57A7D
ZU52GDX3DU9M
ZU52HTNZ16E8
ZU52VO0615MW
ZU59Q04X6JPO
ZU59Y0ECW77O
ZU5FACJX4GPD
ZU5GSICCP0DK
ZU5N8YE27IS7
ZU5S5DRSQ06U
ZU5YV7LAGLRC
ZU5Z9B20I4O8
ZU64EXB7HUSC
ZU6H43BW484F
ZU75EZTKCB97
ZU7JIT3YEPV3
ZU7WLZ4WQ44X
ZU8123A1UF26
ZU81ZUXRWG49
ZU85FAS6WKIS
ZU86EVPYWRRJ
ZU88JQ8P2SDV
ZU8KDIBLI5W6